# Озвучивание текста

## Загрузка необходимых библиотек

Сегодня рассмотрим такую проблему, как перевод текстовой информации в голосовое сообщение.

Для начала загрузим необходимые библиотеки, а также отключим проверку сертификата, как в других заданиях.

In [4]:
import ssl

In [5]:
ssl._create_default_https_context = ssl._create_unverified_context

In [1]:
import sys
!{sys.executable} -m pip install torch torchaudio omegaconf

Defaulting to user installation because normal site-packages is not writeable
     |████████████████████████████████| 3.3 MB 1.7 MB/s eta 0:00:01
     |████████████████████████████████| 79 kB 31.1 MB/s eta 0:00:01
     |████████████████████████████████| 117 kB 71.5 MB/s eta 0:00:01
Using legacy setup.py install for antlr4-python3-runtime, since package 'wheel' is not installed.
    Running setup.py install for antlr4-python3-runtime ... done
You should consider upgrading via the '/usr/local/bin/python3.7 -m pip install --upgrade pip' command.


In [4]:
import os

import wave
import torch
import contextlib

from omegaconf import OmegaConf
from IPython.display import Audio, display

torch — широкоиспользуемая библиотека для работы с машинным обучением. torch.hub является своего рода хранилищем с обученными моделями для самых разных проблем. В большинстве случаев достаточно скачать модель, обученную на большом количестве данных, и немного изменить ее, подстроив под свою проблему. Из этого может получится хорошая отправная точка для нахождения оптимального решения.

Загрузив библиотеки, нужно скачать модели silero-models. Ты можешь подробнее ознакомиться с ними на их сайте (либо в github).

In [5]:
torch.hub.download_url_to_file(
    'https://raw.githubusercontent.com/snakers4/silero-models/master/models.yml',
    'latest_silero_models.yml',
    progress=False
)
models = OmegaConf.load('latest_silero_models.yml')

## Модели silero

Посмотрим, какие языки поддерживаются этими моделями. Разные модели могут работать с определённым набором языков. Все зависит от данных, на которых училась каждая модель.

In [6]:
available_languages = list(models.tts_models.keys())
print(f'Available languages {available_languages}')

Available languages ['ru', 'en', 'de', 'es', 'fr', 'ba', 'xal', 'tt', 'uz', 'ua', 'indic', 'multi']


Посмотрим на возможные модели для каждого из языков.

In [7]:
for lang in available_languages:
    _models = list(models.tts_models.get(lang).keys())
    print(f'Модели для {lang}: {_models}')

Модели для ru: ['v3_1_ru', 'ru_v3', 'aidar_v2', 'aidar_8khz', 'aidar_16khz', 'baya_v2', 'baya_8khz', 'baya_16khz', 'irina_v2', 'irina_8khz', 'irina_16khz', 'kseniya_v2', 'kseniya_8khz', 'kseniya_16khz', 'natasha_v2', 'natasha_8khz', 'natasha_16khz', 'ruslan_v2', 'ruslan_8khz', 'ruslan_16khz']
Модели для en: ['v3_en', 'v3_en_indic', 'lj_v2', 'lj_8khz', 'lj_16khz']
Модели для de: ['v3_de', 'thorsten_v2', 'thorsten_8khz', 'thorsten_16khz']
Модели для es: ['v3_es', 'tux_v2', 'tux_8khz', 'tux_16khz']
Модели для fr: ['v3_fr', 'gilles_v2', 'gilles_8khz', 'gilles_16khz']
Модели для ba: ['aigul_v2']
Модели для xal: ['v3_xal', 'erdni_v2']
Модели для tt: ['v3_tt', 'dilyara_v2']
Модели для uz: ['v3_uz', 'dilnavoz_v2']
Модели для ua: ['v3_ua', 'mykyta_v2']
Модели для indic: ['v3_indic']
Модели для multi: ['multi_v2']


В данном случае нас интересует русский язык. Выведем модели, которые подходят для нашей задачи.

In [8]:
_models = list(models.tts_models.get('ru').keys())
print(f'Модели для русского языка: {_models}')

Модели для русского языка: ['v3_1_ru', 'ru_v3', 'aidar_v2', 'aidar_8khz', 'aidar_16khz', 'baya_v2', 'baya_8khz', 'baya_16khz', 'irina_v2', 'irina_8khz', 'irina_16khz', 'kseniya_v2', 'kseniya_8khz', 'kseniya_16khz', 'natasha_v2', 'natasha_8khz', 'natasha_16khz', 'ruslan_v2', 'ruslan_8khz', 'ruslan_16khz']


## Загрузка модели

Выберем модель v3_1_ru. Работа на компьютере может осуществляться на CPU или на GPU (намного быстрее в случае работы с моделями машинного обучения). Для простоты укажем, что мы будем работать на CPU.

In [9]:
language = 'ru'
model_id = 'v3_1_ru'
sample_rate = 48000
device = torch.device('cpu')

Создадим модель с параметрами выше. В переменную example_text будет скачан базовый пример текста для тестирования.

In [10]:
model, example_text = torch.hub.load(
    repo_or_dir='snakers4/silero-models',
    model='silero_tts',
    language=language,
    speaker=model_id
)
model.to(device)  # gpu or cpu

Downloading: "https://github.com/snakers4/silero-models/archive/master.zip" to /root/.cache/torch/hub/master.zip
100%|██████████| 59.0M/59.0M [00:04<00:00, 13.8MB/s]


### Работа с моделью

Посмотрим, какими голосами может «говорить» наша модель.

In [11]:
model.speakers

['aidar', 'baya', 'kseniya', 'xenia', 'eugene', 'random']

### Text

Укажем скорость записи, выберем говорящего (в данном случае, это женский голос), а также необходимые параметры. Также возьмем небольшую скороговорку, как пример текста.

In [20]:
example_text = 'В недрах тундры выдры в гетрах тырят в вёдра ядра кедров.'

Теперь переведем этот текст в звук.

In [21]:
audio = model.apply_tts(
    text=example_text,
    speaker='aidar',
)
print(example_text)
display(Audio(audio, rate=sample_rate))

В недрах тундры выдры в гетрах тырят в вёдра ядра кедров.


Скорее всего, что-то режет слух. Неудивительно - наша модель ошиблась с ударением. Для этого мы можем выставить ударения в текста, прежде чем он будет преобразован в звук.

In [14]:
example_text = 'В недрах тундры выдры в гетрах тырят в +вёдра +ядра к+едров.'

In [22]:
audio = model.apply_tts(
    text=example_text,
    speaker='xenia',
)
print(example_text)
display(Audio(audio, rate=sample_rate))

В недрах тундры выдры в гетрах тырят в вёдра ядра кедров.


Можно не только изменять ударение, но и очень значительно изменять манеру говорения: повышать или понижать тон, замедлять или ускорять темп, делать паузы. Изучи пример ниже.

In [23]:
ssml_sample = """
              <speak>
              <p>
                  Когда я просыпаюсь, <prosody rate="x-slow">я говорю довольно медленно</prosody>.
                  Потом я начинаю говорить своим обычным голосом,
                  <prosody pitch="x-high"> а могу говорить тоном выше </prosody>,
                  или <prosody pitch="x-low">наоборот, ниже</prosody>.
                  Потом, если повезет, <prosody rate="fast">я могу говорить и довольно быстро.</prosody>
                  А еще я умею делать паузы любой длины, например, две секунды <break time="2000ms"/>.
                  <p>
                    Также я умею делать паузы между параграфами.
                  </p>
                  <p>
                    <s>И также я умею делать паузы между предложениями.</s>
                    <s>Вот, например, как сейчас.</s>
                  </p>
              </p>
              </speak>
              """

audio = model.apply_tts(
    ssml_text=ssml_sample,
    speaker='xenia',
)
display(Audio(audio, rate=sample_rate))

## Задание 1

Сегодня тебе не нужно будет обучать новые модели. Твое задание заключается в следующем:

Составь небольшую речь, используя примеры выше, и преобразуй ее в звуковой файл.
1. Выбери подходящий голос для озвучивания.
2. Необходимо, чтобы все ударения были правильно проставлены.
3. Используй как можно больше модификаций голоса. Минимум 4 модификации (про них более подробно можешь прочитать [здесь](https://github.com/snakers4/silero-models/wiki/SSML)).
4. Сохрани получившийся аудио-файл.